In [3]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import seaborn as sns
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier  # ou KNeighborsRegressor si c'est une régression
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics.pairwise import cosine_similarity, euclidean_distances
from sklearn.preprocessing import MinMaxScaler

In [4]:
df = pd.read_csv("df_sans_vec.csv")

In [5]:
df_ml  = df[["originalTitle","numVotes","averageRating","startYear","genres","jobs","noms"]]

In [6]:
df_ml["age_film"] = - (df_ml["startYear"] - 2025)

C:\Users\valen\AppData\Local\Temp\ipykernel_21308\3775384337.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_ml["age_film"] = - (df_ml["startYear"] - 2025)


In [7]:
df_ml = df_ml.set_index(df_ml["originalTitle"]+"_"+df_ml["startYear"].astype(str))

In [8]:
df_ml = df_ml.drop(["startYear", "originalTitle"], axis=1)

In [9]:
df_ml.head()

numVotes  averageRating  \
Partie de campagne_1946               7427            7.5   
Kate & Leopold_2001                  91790            6.4   
The Best Years of Our Lives_1946     74474            8.1   
Anchors Aweigh_1945                   9755            7.0   
And Then There Were None_1945        17602            7.4   

                                                      genres  \
Partie de campagne_1946             {'Comedy,Drama,Romance'}   
Kate & Leopold_2001               {'Comedy,Fantasy,Romance'}   
The Best Years of Our Lives_1946       {'Drama,Romance,War'}   
Anchors Aweigh_1945               {'Comedy,Fantasy,Musical'}   
And Then There Were None_1945        {'Crime,Drama,Mystery'}   

                                                                               jobs  \
Partie de campagne_1946           ['actress', 'actress', 'actor', 'actor', 'acto...   
Kate & Leopold_2001               ['actress', 'actor', 'actor', 'actor', 'actres...   
The Best Years of Our Lives_1946  ['actress', 'actor', 'actor', 'actress', 'actr...   
Anchors Aweigh_1945               ['actor', 'actress', 'actor', 'actor', 'actor'...   
And Then There Were None_1945     ['actor', 'actor', 'actor', 'actor', 'actress'...   

                                                                               noms  \
Partie de campagne_1946           ['Sylvia Bataille', 'Jane Marken', "Georges D'...   
Kate & Leopold_2001               ['Meg Ryan', 'Hugh Jackman', 'Liev Schreiber',...   
The Best Years of Our Lives_1946  ['Myrna Loy', 'Dana Andrews', 'Fredric March',...   
Anchors Aweigh_1945               ['Frank Sinatra', 'Kathryn Grayson', 'Gene Kel...   
And Then There Were None_1945     ['Barry Fitzgerald', 'Walter Huston', 'Louis H...   

                                  age_film  
Partie de campagne_1946                 79  
Kate & Leopold_2001                     24  
The Best Years of Our Lives_1946        79  
Anchors Aweigh_1945                     80  
And Then There Were None_1945           80

In [10]:
df_ml["genres"] = df_ml["genres"].apply(lambda genre_str:genre_str[1:-1].replace("'","").split(","))

In [11]:
df_ml["genres"].iloc[0]

['Comedy', 'Drama', 'Romance']

In [12]:
mlb = MultiLabelBinarizer()
df_cat = pd.DataFrame(mlb.fit_transform(df_ml["genres"]), columns=mlb.classes_, index=df_ml.index)

In [13]:
df_ml = pd.concat([df_ml, df_cat], axis = 1)

In [14]:
df_cat.head()

Action  Adventure  Animation  Biography  \
Partie de campagne_1946                0          0          0          0   
Kate & Leopold_2001                    0          0          0          0   
The Best Years of Our Lives_1946       0          0          0          0   
Anchors Aweigh_1945                    0          0          0          0   
And Then There Were None_1945          0          0          0          0   

                                  Comedy  Crime  Documentary  Drama  Family  \
Partie de campagne_1946                1      0            0      1       0   
Kate & Leopold_2001                    1      0            0      0       0   
The Best Years of Our Lives_1946       0      0            0      1       0   
Anchors Aweigh_1945                    1      0            0      0       0   
And Then There Were None_1945          0      1            0      1       0   

                                  Fantasy  ...  Musical  Mystery  News  \
Partie de campagne_1946                 0  ...        0        0     0   
Kate & Leopold_2001                     1  ...        0        0     0   
The Best Years of Our Lives_1946        0  ...        0        0     0   
Anchors Aweigh_1945                     1  ...        1        0     0   
And Then There Were None_1945           0  ...        0        1     0   

                                  Romance  Sci-Fi  Short  Sport  Thriller  \
Partie de campagne_1946                 1       0      0      0         0   
Kate & Leopold_2001                     1       0      0      0         0   
The Best Years of Our Lives_1946        1       0      0      0         0   
Anchors Aweigh_1945                     0       0      0      0         0   
And Then There Were None_1945           0       0      0      0         0   

                                  War  Western  
Partie de campagne_1946             0        0  
Kate & Leopold_2001                 0        0  
The Best Years of Our Lives_1946    1        0  
Anchors Aweigh_1945                 0        0  
And Then There Were None_1945       0        0  

[5 rows x 24 columns]

In [15]:
compteur_real = {}
compteur_acteurs =  {}
for i, row in df_ml.iterrows():
  try:
    names = eval(row["noms"])
    jobs = eval(row["jobs"])
    for name, job in zip(names, jobs):
      if job == "actress":
        if name not in compteur_acteurs:
            compteur_acteurs[name] = 1
        else:
            compteur_acteurs[name]+=1
      if job == "actor":
        if name not in compteur_acteurs:
          compteur_acteurs[name] = 1
        else:
          compteur_acteurs[name]+=1
      if job == "director":
        if name not in compteur_real:
          compteur_real[name] = 1
        else:
          compteur_real[name]+=1
  except:
    pass

  dico_acteurs = dict(sorted(compteur_acteurs.items(), key=lambda x: x[1], reverse=True)[:500])
  dico_real = dict(sorted(compteur_real.items(), key=lambda x: x[1], reverse=True)[:500])

In [16]:
from numpy import zeros

In [17]:
for acteur in dico_acteurs.keys():
  df_ml[f"actor_{acteur}"] = zeros(df_ml.shape[0])
for real in dico_real.keys():
  df_ml[f"real_{real}"] = zeros(df_ml.shape[0])

C:\Users\valen\AppData\Local\Temp\ipykernel_21308\1052391298.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_ml[f"actor_{acteur}"] = zeros(df_ml.shape[0])
C:\Users\valen\AppData\Local\Temp\ipykernel_21308\1052391298.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_ml[f"actor_{acteur}"] = zeros(df_ml.shape[0])
C:\Users\valen\AppData\Local\Temp\ipykernel_21308\1052391298.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performanc

In [18]:
def remplir_donnees_real_acteurs(row):
  try:
    names = eval(row["noms"]) # liste des noms des personnes qui ont travaillé dans le film
    jobs = eval(row["jobs"]) # leur job
    for name, job in zip(names, jobs):
      if (job == "actor" or job == "actress") and name in dico_acteurs:
        row[f"actor_{name}"] = 1
      if job == "director" and name in dico_real:
        row[f"real_{name}"] = 1
  except:
    pass
  return row

In [19]:
df_ml = df_ml.apply(remplir_donnees_real_acteurs, axis=1)

In [20]:
df_ml=df_ml.fillna(0)

In [21]:
df_ml.loc["Gladiator_2000"]["actor_Russell Crowe"]

np.float64(1.0)

In [22]:
Z = df_ml[["numVotes", "averageRating", "age_film"]]

In [23]:
scaler = MinMaxScaler(feature_range=(0, 1))
X_scaled = scaler.fit_transform(Z)


In [24]:
X_scaled

array([[7.98605830e-04, 7.83132530e-01, 9.87500000e-01],
       [2.85697450e-02, 6.50602410e-01, 3.00000000e-01],
       [2.28695560e-02, 8.55421687e-01, 9.87500000e-01],
       ...,
       [3.22602520e-05, 7.22891566e-01, 6.25000000e-02],
       [5.03786629e-03, 6.26506024e-01, 5.00000000e-02],
       [3.42682881e-04, 6.50602410e-01, 6.25000000e-02]], shape=(17526, 3))

In [25]:
df_ml[["numVotes", "averageRating", "age_film"]] = X_scaled

In [26]:
df_ml

numVotes  averageRating  \
Partie de campagne_1946           0.000799       0.783133   
Kate & Leopold_2001               0.028570       0.650602   
The Best Years of Our Lives_1946  0.022870       0.855422   
Anchors Aweigh_1945               0.001565       0.722892   
And Then There Were None_1945     0.004148       0.771084   
...                                    ...            ...   
Coffee & Kareem_2020              0.003263       0.506024   
Kaithi_2019                       0.013695       0.891566   
Herself_2020                      0.000032       0.722892   
Eight for Silver_2021             0.005038       0.626506   
Akelarre_2020                     0.000343       0.650602   

                                                      genres  \
Partie de campagne_1946             [Comedy, Drama, Romance]   
Kate & Leopold_2001               [Comedy, Fantasy, Romance]   
The Best Years of Our Lives_1946       [Drama, Romance, War]   
Anchors Aweigh_1945               [Comedy, Fantasy, Musical]   
And Then There Were None_1945        [Crime, Drama, Mystery]   
...                                                      ...   
Coffee & Kareem_2020                 [Action, Comedy, Crime]   
Kaithi_2019                        [Action, Crime, Thriller]   
Herself_2020                                         [Drama]   
Eight for Silver_2021             [Fantasy, Horror, Mystery]   
Akelarre_2020                               [Drama, History]   

                                                                               jobs  \
Partie de campagne_1946           ['actress', 'actress', 'actor', 'actor', 'acto...   
Kate & Leopold_2001               ['actress', 'actor', 'actor', 'actor', 'actres...   
The Best Years of Our Lives_1946  ['actress', 'actor', 'actor', 'actress', 'actr...   
Anchors Aweigh_1945               ['actor', 'actress', 'actor', 'actor', 'actor'...   
And Then There Were None_1945     ['actor', 'actor', 'actor', 'actor', 'actress'...   
...                                                                             ...   
Coffee & Kareem_2020              ['actor', 'actress', 'actor', 'actress', 'acto...   
Kaithi_2019                       ['actor', 'actor', 'actor', 'actor', 'actor', ...   
Herself_2020                      ['actress', 'actress', 'actress', 'actor', 'ac...   
Eight for Silver_2021             ['actor', 'actress', 'actor', 'actress', 'acto...   
Akelarre_2020                     ['actress', 'actor', 'actor', 'actress', 'actr...   

                                                                               noms  \
Partie de campagne_1946           ['Sylvia Bataille', 'Jane Marken', "Georges D'...   
Kate & Leopold_2001               ['Meg Ryan', 'Hugh Jackman', 'Liev Schreiber',...   
The Best Years of Our Lives_1946  ['Myrna Loy', 'Dana Andrews', 'Fredric March',...   
Anchors Aweigh_1945               ['Frank Sinatra', 'Kathryn Grayson', 'Gene Kel...   
And Then There Were None_1945     ['Barry Fitzgerald', 'Walter Huston', 'Louis H...   
...                                                                             ...   
Coffee & Kareem_2020              ['Ed Helms', 'Taraji P. Henson', 'Terrence Lit...   
Kaithi_2019                       ['Karthi', 'Narain', 'Arjun Das', 'George Mary...   
Herself_2020                      ['Molly McCann', 'Clare Dunne', "Ruby Rose O'H...   
Eight for Silver_2021             ['Boyd Holbrook', 'Kelly Reilly', 'Alistair Pe...   
Akelarre_2020                     ['Amaia Aberasturi', 'Alex Brendemühl', 'Danie...   

                                  age_film  Action  Adventure  Animation  \
Partie de campagne_1946             0.9875       0          0          0   
Kate & Leopold_2001                 0.3000       0          0          0   
The Best Years of Our Lives_1946    0.9875       0          0          0   
Anchors Aweigh_1945                 1.0000       0          0          0   
And Then There Were None_1945       1.0000       0          0 

In [27]:
X = df_ml.drop(["jobs","genres","noms"], axis = 1)

In [28]:
ml_cos = cosine_similarity(X)

In [29]:
ml_cos.shape

(17526, 17526)

In [30]:
ml_cos = pd.DataFrame(ml_cos, index= df_ml.index, columns=df_ml.index)

In [31]:
ml_cos.head()

Partie de campagne_1946  \
Partie de campagne_1946                          1.000000   
Kate & Leopold_2001                              0.448902   
The Best Years of Our Lives_1946                 0.712286   
Anchors Aweigh_1945                              0.507286   
And Then There Were None_1945                    0.564381   

                                  Kate & Leopold_2001  \
Partie de campagne_1946                      0.448902   
Kate & Leopold_2001                          1.000000   
The Best Years of Our Lives_1946             0.265882   
Anchors Aweigh_1945                          0.404014   
And Then There Were None_1945                0.128194   

                                  The Best Years of Our Lives_1946  \
Partie de campagne_1946                                   0.712286   
Kate & Leopold_2001                                       0.265882   
The Best Years of Our Lives_1946                          1.000000   
Anchors Aweigh_1945                                       0.286043   
And Then There Were None_1945                             0.516943   

                                  Anchors Aweigh_1945  \
Partie de campagne_1946                      0.507286   
Kate & Leopold_2001                          0.404014   
The Best Years of Our Lives_1946             0.286043   
Anchors Aweigh_1945                          1.000000   
And Then There Were None_1945                0.309180   

                                  And Then There Were None_1945  \
Partie de campagne_1946                                0.564381   
Kate & Leopold_2001                                    0.128194   
The Best Years of Our Lives_1946                       0.516943   
Anchors Aweigh_1945                                    0.309180   
And Then There Were None_1945                          1.000000   

                                  The Bells of St. Mary's_1945  \
Partie de campagne_1946                               0.750881   
Kate & Leopold_2001                                   0.168432   
The Best Years of Our Lives_1946                      0.687404   
Anchors Aweigh_1945                                   0.409731   
And Then There Were None_1945                         0.751402   

                                  The Body Snatcher_1945  \
Partie de campagne_1946                         0.345226   
Kate & Leopold_2001                             0.127186   
The Best Years of Our Lives_1946                0.320285   
Anchors Aweigh_1945                             0.308069   
And Then There Were None_1945                   0.345729   

                                  Brief Encounter_1945  \
Partie de campagne_1946                       0.784588   
Kate & Leopold_2001                           0.291952   
The Best Years of Our Lives_1946              0.715300   
Anchors Aweigh_1945                           0.315568   
And Then There Were None_1945                 0.569646   

                                  Christmas in Connecticut_1945  \
Partie de campagne_1946                                0.884252   
Kate & Leopold_2001                                    0.506331   
The Best Years of Our Lives_1946                       0.583658   
Anchors Aweigh_1945                                    0.573510   
And Then There Were None_1945                          0.391092   

                                  Conflict_1945  ...  \
Partie de campagne_1946                0.561552  ...   
Kate & Leopold_2001                    0.125159  ...   
The Best Years of Our Lives_1946       0.513942  ...   
Anchors Aweigh_1945                    0.305809  ...   
And Then There Were None_1945          0.780924  ...   

                                  Malang - Unleash the Madness_2020  \
Partie de campagne_1946                                    0.350080   
Kate & Leopold_2001                                        0.073156   
The Best Years of Our Lives_1946                           0.323416   
Anchors Aweigh_1945       

In [40]:
def reco_films(titre):
    liste=[]
    sim_scores = ml_cos.loc[titre]
    sim_indices = np.argsort(sim_scores)[::-1][1:11] # Ignore le film lui-même
    for i in sim_indices:
        liste.append(f"{df.iloc[i]['originalTitle']}_{df.iloc[i]['startYear']}")
    return liste

In [ ]:
reco_films("Mononoke-Hime_1997")

KeyError: 'Mononoke-Hime_1997'

In [42]:
recos = {}
id_films = df['originalTitle']+"_"+df['startYear'].astype(str)

for id_film in id_films:
    reco = reco_films(id_film)
    recos[id_film] = reco
recos

{'Partie de campagne_1946': ['Born Yesterday_1950',
  'Le plaisir_1952',
  'How to Marry a Millionaire_1953',
  'Auntie Mame_1958',
  'Bus Stop_1956',
  'Lover Come Back_1961',
  "Divorzio all'italiana_1961",
  'Love with the Proper Stranger_1963',
  'Ostre sledované vlaky_1966',
  'Deep End_1970'],
 'Kate & Leopold_2001': ["It's a Boy Girl Thing_2006",
  'Teen Witch_1989',
  '18 Again!_1988',
  'Mannequin_1987',
  'The Heavenly Kid_1985',
  'Bana Masal Anlatma_2015',
  'When We First Met_2018',
  'Je ne suis pas un homme facile_2018',
  'Liza, a rókatündér_2015',
  'Status Update_2018'],
 'The Best Years of Our Lives_1946': ['The Heiress_1949',
  'Letyat zhuravli_1957',
  'Popiól i diament_1958',
  'Ballada o soldate_1959',
  'Mughal-E-Azam_1960',
  'War and Peace_1956',
  'Voyna i mir_1965',
  'Voor een verloren soldaat_1992',
  'Indochine_1992',
  'Pred dozhdot_1994'],
 'Anchors Aweigh_1945': ['Bye Bye Birdie_1963',
  'Viva Las Vegas_1964',
  'Magical Mystery Tour_1967',
  "Peau d'â

In [45]:
df_reco = pd.json_normalize(recos).T
df_reco.columns = ["recos"]

In [47]:
df_reco.to_csv("reco_film.csv")

In [49]:
df_reco

recos
Partie de campagne_1946           [Born Yesterday_1950, Le plaisir_1952, How to ...
Kate & Leopold_2001               [It's a Boy Girl Thing_2006, Teen Witch_1989, ...
The Best Years of Our Lives_1946  [The Heiress_1949, Letyat zhuravli_1957, Popió...
Anchors Aweigh_1945               [Bye Bye Birdie_1963, Viva Las Vegas_1964, Mag...
And Then There Were None_1945     [Dressed to Kill_1946, Midnight Lace_1960, Pre...
...                                                                             ...
Coffee & Kareem_2020              [Looop Lapeta_2022, Danger One_2018, Inner Cit...
Kaithi_2019                       [Theeran Adhigaaram Ondru_2017, Por Thozhil_20...
Herself_2020                      [Thappad_2020, The Man Who Sold His Skin_2020,...
Eight for Silver_2021             [The Prodigy_2019, Pari_2018, Gretel & Hansel_...
Akelarre_2020                     [Firebrand_2023, Zama_2017, The Eichmann Show_...

[17513 rows x 1 columns]